In [123]:
from coffeetools import coffee
import jinja2 
import IPython
import glob
import json
import pandas
import qgrid
qgrid.nbinstall(overwrite=True)  # copies javascript dependencies to your /nbextensions folder 
qgrid.set_defaults(remote_js=True)

In [124]:
%%html
<script src="https://cdnjs.cloudflare.com/ajax/libs/jquery.isotope/2.2.2/isotope.pkgd.min.js"></script>

* Use [IsotopeJS](http://isotope.metafizzy.co) to filter bootstrap panels at top level
    Sort by: Stars, Forks, Commits, slocs, Languages
* Bokeh plot for code commits and code frequency
* Connect contributors in a [network graph](http://nbviewer.ipython.org/gist/tonyfast/e4e22f4bc261a2ae0c42)
    _This network examples connects repositories by user actions on Github._

In [125]:
%%html
<div class="button-group sort-by-button-group">
  <button data-sort-by="original-order">original order</button>
  <button data-sort-by="name">name</button>
  <button data-sort-by="symbol">symbol</button>
  <button data-sort-by="number">number</button>
  <button data-sort-by="weight">weight</button>
  <button data-sort-by="category">category</button>
</div>

In [126]:
rows = []
for user in glob.glob('darpa-github/*'):
    for repo in glob.glob( user +'/*'):
        current = {
            'lang':{},
        }
        with open(repo + '/languages','r') as f:
            _d = json.load(f)
            
            if all( [isinstance(a,int) for a in _d.values()]):
                current['sloc'] = sum(_d.values())
                for k,v in _d.items():
                    current['lang'][k] = v/current['sloc']
                
        with open(repo + '/info','r') as f:            
            for k,v in json.load(f).items():
                if k.endswith('_count') or k.endswith('_at') or k in ['url','description']:
                    current[k] = v
        with open(repo + '/contributors','r') as f:            
            current['contributors_count'] = len(json.load(f))
        if current:
            rows.append( current )

In [127]:
df = pandas.io.json.json_normalize(rows).fillna(0)

In [128]:
qgrid.show_grid(df[[c for c in df.columns if not c.startswith('lang')]])